# Named Entity Recognition with Flair for CLS

This Notebook shows you how to perform NER and/or aspect recognition on your data using the NLP-library Flair. This Notebook gives you a general overview of how to perform NER with the Natural Language Processing framework Flair for literary-historical texts in **English**, **French**, **German** and **Dutch** in different scenarios:

1.   You do not have any labelled data to train your own NER-system, and the entities you want to recognize are part of the spaCy models.
Generic NER through Flair for French, Dutch, German and English.

    *   Apply generic entity recognition using Flair's off-the-shelf models for English, Dutch, French and German.


2.   You do not have any labelled data to train your own NER-system, but you do want to recognize domain-specific entities which are not part of the Flair's models

    * Apply NER/aspect recognition using Flair's off-the-shelf [zero-shot model TARS](https://aclanthology.org/2020.coling-main.285/).  


3.   You have enough annotations available to train your own pipeline to recognize domain-specific entities.
     *   Train a SequenceClassifier with adequate embeddings from HuggingFace.
     *   Evaluate the performance on a held-out test set.








## Input and output


The notebook starts with **.txt-files** as input, and outputs a **.csv-file** in the following structure:

Text_name | Entity_text | Entity_sentence | Entity_category
-------------|------------|------------|------------
file.txt      |Rome| All roads lead to Rome. | LOCATION


---

📜🎓 **Side-note for the commmon good**

Are these methods all-encompassing? **No**.

Do we need to be full-fledged NLP-engineers to apply information extraction? **Not really**.

Do we need to know the pitfalls of applying these methods to our texts? **Big yes**.

Is the NLP-landscape currently changing at hyperspeed and may this Notebook be outdated when I read it? **Humongous yes**.

❗ So take this notebook as an example for you to build on, an example of how things **can** be done and not how they **should** be done. Don't stop exploring and learning, and remember that experimentation is the name of the game. There is [no such thing as a free lunch](https://en.wikipedia.org/wiki/No_free_lunch_theorem#:~:text=In%20mathematical%20folklore%2C%20the%20%22no,Free%20Lunch%20Theorems%20for%20Optimization%22.), and the same goes for modelling.

["*All models are wrong, some are useful*."](https://en.wikipedia.org/wiki/All_models_are_wrong)




---
❗🎓 To adapt and use this Notebook to produce entities for your own texts, you need to have an intuitive understanding of the following concepts:



*   [named entity recognition](https://en.wikipedia.org/wiki/Named-entity_recognition)
*   few-shot modelling
*   zero-shot modelling
*   Large Language Models (generative AI)
*   [HuggingFace model hub](https://huggingface.co/)
*   [BIO-labels / span evaluation](https://pypi.org/project/nervaluate/)
*   Evaluation metrics (F1, accuracy, precision, recall)
*   GitHub
*   [Flair](https://flairnlp.github.io/)


To adapt the code, you need to know about:


* Functions in Python
* Pandas dataframe operations
* Jupyter Notebooks





# Load data

In [ ]:
!pip install flair

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 388.3/388.3 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.3/139.3 kB 17.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.4/54.4 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.7/19.7 MB 70.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 78.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 202.6/202.6 kB 30.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.8/143.8 kB 23.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 51.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.2/82.2 kB 13.0 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3

In [ ]:
import pandas as pd
import os
import glob

from flair.nn import Classifier
from flair.splitter import SegtokSentenceSplitter
from tqdm.auto import tqdm

from flair.data import Corpus
from flair.models import TARSTagger, FewshotClassifier
from flair.trainers import ModelTrainer
from flair.datasets import ColumnCorpus
from flair.data import Sentence
import torch



tqdm.pandas()

In [ ]:
!git clone https://github.com/TessDejaeghere/example_data_CLS.git

Cloning into 'example_data_CLS'...
remote: Enumerating objects: 55, done.
remote: Counting objects: 100% (55/55), done.
remote: Compressing objects: 100% (55/55), done.
remote: Total 55 (delta 3), reused 0 (delta 0), pack-reused 0
Receiving objects: 100% (55/55), 7.46 MiB | 5.49 MiB/s, done.
Resolving deltas: 100% (3/3), done.


In [ ]:
path = "/content/example_data_CLS/"

In [ ]:
all_travelogues = []

for filename in glob.glob(f"{path}*/*.txt"):

  name_file = os.path.basename(filename) #find filename
  folder_name = os.path.dirname(filename).split("/")[-1] #find folder name (in our case: the language)

  with open(filename, "r") as travelogue:

    text = travelogue.read()
    travelogue_data = {"file": name_file, "text": text, "language": folder_name}
    all_travelogues.append(travelogue_data)

travel_df = pd.DataFrame(all_travelogues)

In [ ]:
#let's have a look at our data!
travel_df.sample(10)

file  \
34                                      Rome.txt   
33  Florence_and_Northern_Tuscany_with_Genoa.txt   
39                 Roman_Holidays_and_Others.txt   
14                                    TP1179.txt   
24                          woen003aant01_01.txt   
7                                    58063-0.txt   
21                          gerr049besc01_01.txt   
29                          haff003reiz01_01.txt   
38                 Cathedral_Cities_of_Italy.txt   
6                                    pg15556.txt   

                                                 text language  
34  Title: Rome\nAuthor: Mildred Anna Rosalie Tuke...  English  
33  Title: Florence and Northern Tuscany with Geno...  English  
39  Title: Roman Holidays and Others\nAuthor: W. D...  English  
14  Author: Wollstonecraft Mary \nTitle: Briefe ge...   German  
24  GEBRUIKT EXEMPLAAR exemplaar universiteitsbibl...    Dutch  
7   ﻿The Project Gutenberg EBook of Voyage en Espa...   French  
21  2016 dbnl Hessel Gerritsz, Beschryvinghe vande...    Dutch  
29  ﻿\n\n\n\n\n\nReize in eenen palanquin, of Lotg...    Dutch  
38  Title: Cathedral Cities of Italy\nAuthor: Will...  English  
6   ﻿The Project Gutenberg EBook of Voyages en Fra...   French

In [ ]:
#let's have a look at how many texts we have per language!
travel_df["language"].value_counts()

language
French     10
German     10
Dutch      10
English    10
Name: count, dtype: int64

In [ ]:
#Make separate corpora per language
English_corpus = travel_df[travel_df["language"] == "English"]
Dutch_corpus = travel_df[travel_df["language"] == "Dutch"]
German_corpus = travel_df[travel_df["language"] == "German"]
French_corpus = travel_df[travel_df["language"] == "French"]

# Generic NER (German)

Flair hosts [different models for French, Dutch, German and English](https://flairnlp.github.io/docs/tutorial-basics/tagging-entities). Each of these models ships with different entity labels. The names of the models refer to their underlying architecture (e.g.: 'rnn' refers to 'recurrent neural network'), the size of their training data (e.g.: 'large') or the data it was trained on (e.g.: 'ontonotes').

Language | Model name
-------------|------------
English      |ner-fast, ner-large, ner-pooled, ner-ontonotes
Dutch        |nl-ner, nl-ner-large, nl-ner-rnn
German         |de-ner, de-ner-large
French         |fr-ner


Most models work with a four-label system, and only recognize PERSON, LOCATION, ORGANISATION and MISC (miscellaneous).



In [ ]:
German_corpus.head()

file                                               text language
10   TP938.txt  Author: Hearne Samuel\nTitle: Reise vom Fort P...   German
11  TP1213.txt  Author: LeBeau Claude\nTitle: Neue Reise unter...   German
12  TP1027.txt  Author: nan\nTitle: Begebenheiten eines Reisen...   German
13   TP934.txt  Author: nan\nTitle: Anmerkungen eines reisende...   German
14   TP930.txt  Author: Hirschfeld Christian Cay Lorenz \nTitl...   German

## Labelling our corpus
Let's apply the German model to our dataset, and check the results!

In [ ]:
# initialize sentence splitter
splitter = SegtokSentenceSplitter()

In [ ]:
def ner_german(text, model = 'de-ner'):
  sentences = splitter.split(text) # We split the text into sentences to feed to the model.

  #predict tags
  tagger = Classifier.load('de-ner')
  tagger.predict(sentences)

  output = []
  for sentence in sentences:
    for entity in sentence.get_spans('ner'):
      ent_label = entity.tag
      ent_text = entity.text

      output.append((ent_label, ent_text, sentence.text))
  return output

Let's have a look at what the output looks like! We pass one sentence to our new function to test out the tagger. We get the results in a list of tuples, where each tuple is formatted according to ("LABEL", "text", "sentence").

In [ ]:
ner_german("Ich bin Tess. Ich habe ein Haus in Belgien.")

2024-04-29 15:27:52,648 SequenceTagger predicts: Dictionary with 19 tags: O, S-LOC, B-LOC, E-LOC, I-LOC, S-PER, B-PER, E-PER, I-PER, S-ORG, B-ORG, E-ORG, I-ORG, S-MISC, B-MISC, E-MISC, I-MISC, <START>, <STOP>


[('PER', 'Tess', 'Ich bin Tess.'),
 ('LOC', 'Belgien', 'Ich habe ein Haus in Belgien.')]

That seems to work! It extracts Tess as a PER-entity and Belgien as a LOC. Let's apply this function to a sample of our travelogues DataFrame corpus. We're saving the results in a new column called "results", which will contain all the extracted PEOPLE, ORGANISATIONS, LOCATIONS and MISCELLANEOUS in the list format.



---



❓💭 **Tqdm** is a neat package which allows you to print progress bars while a process is running, so you know how long you'll have to wait. It has a method in the Pandas data science library which we can use to print a progress bar when we're applying a function to our dataframe.

❓💭 We will see the message "an empty Sentence was created! Are there empty strings in your dataset?". Indeed, while parsing the document into sentences, the SentenceSplitter may run into some empty samples. Whether or not this happens depends on your pre-processing steps, and on the way the model parses its sentences from the texts.


🕐 This takes a while!

In [ ]:
German_corpus_sample = German_corpus[0:2]

In [ ]:
German_corpus_sample['results'] = German_corpus_sample.text.progress_apply(ner_german)

  0%|          | 0/2 [00:00<?, ?it/s]

2024-04-29 15:30:06,835 Warning: An empty Sentence was created! Are there empty strings in your dataset?
2024-04-29 15:30:14,130 SequenceTagger predicts: Dictionary with 19 tags: O, S-LOC, B-LOC, E-LOC, I-LOC, S-PER, B-PER, E-PER, I-PER, S-ORG, B-ORG, E-ORG, I-ORG, S-MISC, B-MISC, E-MISC, I-MISC, <START>, <STOP>
2024-04-29 15:44:22,193 Warning: An empty Sentence was created! Are there empty strings in your dataset?
2024-04-29 15:44:30,710 SequenceTagger predicts: Dictionary with 19 tags: O, S-LOC, B-LOC, E-LOC, I-LOC, S-PER, B-PER, E-PER, I-PER, S-ORG, B-ORG, E-ORG, I-ORG, S-MISC, B-MISC, E-MISC, I-MISC, <START>, <STOP>


<ipython-input-22-6c63d414deeb>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  German_corpus_sample['results'] = German_corpus_sample.text.progress_apply(ner_german)


## Inspecting the results

In [ ]:
German_corpus_sample.head()

file                                               text language  \
10   TP938.txt  Author: Hearne Samuel\nTitle: Reise vom Fort P...   German   
11  TP1213.txt  Author: LeBeau Claude\nTitle: Neue Reise unter...   German   

                                              results  
10  [(PER, Hearne Samuel Title, Author: Hearne Sam...  
11  [(PER, LeBeau Claude Title, Author: LeBeau Cla...

In [ ]:
German_corpus_sample = German_corpus_sample.explode("results")

In [ ]:
German_corpus_sample['label'], German_corpus_sample['entity'], German_corpus_sample["sentence"] = zip(*German_corpus_sample.results)

In [ ]:
German_corpus_sample.drop("text", axis =1, inplace = True)

In [ ]:
German_corpus_sample.drop("results", axis = 1, inplace = True)

Cycling through the sample will show you the type of mistakes the model makes. Assess whether it's good enough for your use-case, and then proceed to apply it to your entire corpus.

In [ ]:
German_corpus_sample.sample(30)

file language label            entity  \
10   TP938.txt   German   ORG            KIEF 0   
10   TP938.txt   German   PER         Matonabbi   
11  TP1213.txt   German   PER           Manitou   
11  TP1213.txt   German   PER             Anton   
11  TP1213.txt   German   LOC            Canada   
11  TP1213.txt   German   PER              Huce   
11  TP1213.txt   German  MISC       HauptstXIII   
11  TP1213.txt   German   ORG         Wilden Mc   
11  TP1213.txt   German   LOC             Paris   
11  TP1213.txt   German   LOC            Canada   
10   TP938.txt   German   PER       Mundvorrath   
10   TP938.txt   German   PER              Bayo   
10   TP938.txt   German   PER            Clowey   
10   TP938.txt   German   PER  beyder Partheyen   
10   TP938.txt   German   PER          Esquimos   
11  TP1213.txt   German   PER            Ouebec   
11  TP1213.txt   German   PER             Anton   
11  TP1213.txt   German   LOC           America   
10   TP938.txt   German   LOC             Wests   
11  TP1213.txt   German   LOC           America   
10   TP938.txt   German   LOC         Biberbaue   
11  TP1213.txt   German   LOC            Quebec   
11  TP1213.txt   German   LOC         Rotterdam   
11  TP1213.txt   German   PER            Verfac   
11  TP1213.txt   German   PER             Anton   
11  TP1213.txt   German   PER              Flin   
10   TP938.txt   German   ORG                IG   
11  TP1213.txt   German   PER               Han   
11  TP1213.txt   German   LOC            Canada   
10   TP938.txt   German   LOC        Athapuskos   

                                             sentence  
10  MENTEM AUT ET ExCouT FRIT T- - - - - V - KIEF ...  
10  - Den Tag nach unserer Ankunft am Congecas tha...  
11  $. 1. Man erkennet aus gedachten hier gefunden...  
11  Ich rufe den Anton und dem Nicolaus aus allen ...  
11  $. 1. eil meine Bedienung nicht so beträcht- -...  
11  11; (denn Huce heißt ein wilder Schweinskopf) ...  
11                                   „24 HauptstXIII.  
11                                 bey den Wilden Mc.  
11  Wenn aber die Mißionarien in Canada alle ihre ...  
11  Man mag überhaupt fagen, daß Quebec eine sehr ...  
10  27 Mundvorrath zusandte, wir doch nur für zwei...  
10  Das her pflegten sie alle Jahre in großer Anza...  
10  Am 2osten schickte Matonabbi einen feiner Brüd...  
10  Endlich unterbricht einer vor den Aeltes ften ...  
10  Ich konnte mir leicht vorstellen, daß die über...  
11  Jch bewies ihnen, daß sie sich wegen eines Kri...  
11  Der Anton und ich gin- gen also neben diesem k...  
11                       - dieser Reise nach America.  
10  genehm; wir nahmen jetzt unsere Richtung Wests...  
11  16. Der große Fluß Canada, in dem mitternächti...  
10  Die Lage der Biberbaue ist sehr verschieden, W...  
11  Aus dem- jenigen was sie mir gesagt haben, daß...  
11  Allein dieses war nur eine Kleinigkeit für sie...  
11                                   Tanz des Verfac.  
11  Meine Wilden hielten daher, mittler- weile als...  
11  Ich konnte indessen nicht müde werden, diese v...  
10  2 IG) -, wo die Männer Biber gefangen, oder wo...  
11  Kurz, dieser Han- del währete wohl eine halbe ...  
11  Als ich mich nun wieder hinweg begeben wollte,...  
10  - - 145 In der That erfuhr ich bald, daß meine...

In [ ]:
# inspect how many entities were found in our documents
German_corpus_sample["label"].value_counts()

label
PER     879
LOC     434
ORG      80
MISC     42
Name: count, dtype: int64

## Evaluate the results (on a small test set)

Here, we will show you how you can quantitatively evaluate the results of an off-the-shelf tagger using a small set of **gold-standard data**.

If you would want to use Flair's NER-tagger to label your corpus with PER, LOC, ORG or MISC entities, running this quantitative evaluation will help support that decision. Keep in mind that you're applying a tool trained on modern data to a literary-historical dataset, and that your tagging scheme may differ from the one used by Flair. This will have an impact on the scores!


We'll do this in a couple of steps:


*   Load in the gold standard sentences and annotations
*   Apply the off-the-shelf tagger to the sentences
*   Transform the output of both the tagger and the gold standard annotations to BIO (to do that, you can adapt the code we made in our [notebook which transforms entity text and sentence information to IOB](https://colab.research.google.com/drive/1IqA9gi6ExtFQspg4dmzTvmXCupP7KY35?usp=drive_link).
*   Apply **Nervaluate** to calculate F1, accuracy and precision.




---

❓🧠 Why do we use Nervaluate? [Read more about this package and span evaluation metrics in this blog by David Batista](https://www.davidsbatista.net/blog/2018/05/09/Named_Entity_Evaluation/)! He explains in detail what Nervaluate outputs, and why his method provides a more fine-grained evaluation than evaluation at token-level.

💭❗ You can only do this if you have some labelled data available in the categories provided by the off-the-shelf tool. Have a look at existing annotation platforms, their input and output formats and whether the platform is open-source or not. Some examples of open-source annotation platforms to check out:



*   [INCEPTION](https://inception-project.github.io/)
*   [Doccano](https://github.com/doccano/doccano)
*   [FLAT](https://flat.readthedocs.io/en/latest/)
*   [Tecoholic](https://github.com/tecoholic/ner-annotator)
*   [Universal data tool](https://universaldatatool.com/)

For our project at the Computational Literary Studies Project, we used a server instance of INCEPTION which allowed us to share projects - and used the library [Inceptalytics](https://github.com/catalpa-cl/inceptalytics) to get the results in the desired DataFrame format and calculate Inter-Annotator Agreement.





In [ ]:
test_set = pd.read_csv("/content/example_data_CLS/test_set_results.csv")

In [ ]:
true = test_set["iob_gs"].to_list() #get the gold labels
true = [ast.literal_eval(x) for x in true] #make sure every element in your list is also of type 'list'

predicted = test_set["iob_llm"].to_list()
predicted = [ast.literal_eval(x) for x in predicted]

In [ ]:
evaluator = Evaluator(true, predicted, tags=['FAUNA', 'FLORA'], loader="list")
results, results_by_tag = evaluator.evaluate()

In [ ]:
results

# Zero-shot NER with Flair's TARS (English)


As described on their [GitHub repository](https://github.com/flairNLP/flair/tree/master/resources/docs): "Task-aware representation of sentences (TARS) was introduced by [Halder et al. (2020)](https://kishaloyhalder.github.io/pdfs/tars_coling2020.pdf) as a simple and effective method for few-shot and even zero-shot learning for text classification. This means you can classify text without (m)any training examples. This model is implemented in Flair by the TARSClassifier class.".

The zero-shot model **tars-base** is specifically trained for **English**. At the time of writing Flair hasn't made any alternatives for other languages yet.
The Flair team made models for 1) text classification (**TARSClassifier**) and 2) information extraction (**TARSTagger**). The classifier can for example be used to perform sentiment analysis on the sentence-level, while the Tagger is specifically meant for tasks like NER and aspect recognition.

🐱🌺 Let's see what the **TarsTagger** can do for us in a zero-shot setting (in other words: without training data)! Similar to what we did with spaCy's GliNER, we'll ask the model to recognize **fauna** and **flora** in our corpus.

In [ ]:
# 1. Load zero-shot NER tagger
tars = TARSTagger.load('tars-ner')

2024-04-29 18:21:21,173 https://nlp.informatik.hu-berlin.de/resources/models/tars-ner/tars-ner.pt not found in cache, downloading to /tmp/tmp80gsinlm


100%|██████████| 1.32G/1.32G [00:56<00:00, 25.3MB/s]

2024-04-29 18:22:17,918 copying /tmp/tmp80gsinlm to cache at /root/.flair/models/tars-ner.pt


2024-04-29 18:22:23,844 removing temp file /tmp/tmp80gsinlm


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

2024-04-29 18:22:38,848 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity


This lists all the datasets TARS was trained on for the entities it can recognize. The CONLL-, Ontonotes and WNUT datasets were all used. We will add our own labels, and later our own data to this list and introduce it to the model as a new task. Let's see how!

In [ ]:
# This lists all the tasks TARS was trained for.

existing_tasks = tars.list_existing_tasks()

existing_tasks

{'conll-long',
 'conll-short',
 'ontonotes-long',
 'ontonotes-short',
 'wnut_17-long',
 'wnut_17-short'}

First, we'll see how well the model does with a couple of unseen labels. We manually extracted some sentences from our corpus, and ask the model to label them with "animals" and "plants".

We call this new task **fauna_flora**.

In [ ]:
# Let's see how well the model performs on a couple of test sentences from our corpus
sentences = [
    Sentence("My advice rather is to climb at once to the top, at the back of the Pitti and rest in the pretty flower garden on the very summit of the hill, among the lizards."),
    Sentence("Take us the foxes, the little foxes that spoil the vineyards; for our vineyards have tender grapes."),
    Sentence("After much discussion Dandolo replied that they would do so, the terms being that the Venetian vessels should carry 4500 horses and for this they should be paid 85,000 silver marks."),
]

# Define some classes of named entities (here: we pick fauna and flora as classes)
labels = ["animals", "plants"]
tars.add_and_switch_to_new_task('fauna_flora', labels, label_type='ner') #switch to a new task (TARS can do multiple tasks, so you have to define one here!)

# Predict for these classes and print results
for sentence in sentences:
    tars.predict(sentence)
    result = sentence.get_spans("ner")

    for entity in result:
      print(f"Found entity label: {entity.tag}, found entity text: {entity.text}")

2024-04-29 17:51:54,740 Task `fauna_flora` already exists in TARS model. Switching to it.
Found entity label: animals, found entity text: Pitti


# Few-shot NER with Flair's TARS (English)

The model is not that great! As we can see, it didn't recognize "lizards", "foxes", and "horses", as we had expected. Maybe we can make it better by showing the model some examples of how we expect the end result to look.

We'll start by loading in and preparing a dataset in a format Flair's **ModelTrainer** expects.

We need to transform the data into an **IOB-format**. If you want to check out how we transformed our dataframe with an entity text, sentence text and category label to an IOB-labeled text file, have a look at our [Annotations_to_IOB Notebook](https://colab.research.google.com/drive/1IqA9gi6ExtFQspg4dmzTvmXCupP7KY35?usp=drive_link)!

In [ ]:
training_df = pd.read_csv("example_data_CLS/EN_fauna_flora_df.csv")

In [ ]:
# Our training dataset includes references to fauna and flora entities in the English portion of our travel texts.

training_df.sample(10)

Unnamed: 0                                      sentence  \
303         303      GB-116_sample_English_18.txt_18796-18856   
210         210      GB-104_sample_English_20.txt_18372-18512   
482         482                     IT_2_sample.txt_2552-2753   
134         134  BHL_1949_sample_English_18.0.txt_10523-10663   
669         669        GB-108_sample_English_20.txt_9017-9159   
370         370         BHL_869_sample_IAA_20.0.txt_2799-2931   
528         528        GB-111_sample_English_20.txt_1373-1544   
775         775      GB-108_sample_English_20.txt_21707-21814   
437         437                        BHL_NA_IAA.txt_124-437   
381         381         BHL_869_sample_IAA_20.0.txt_1763-1988   

                           text  \
303         Musetela Canadensis   
210                         hay   
482                   cypresses   
134                       horfe   
669                       ferns   
370             Maispflanzungen   
528             western spotted   
775               rhododendrons   
437                 kreupelhout   
381  Farm Nothochlaena Marcmtae   

                                        _sentence_text aspect_cat  
303  Canadian weasel ( _Musetela Canadensis_ ) : 50...      FAUNA  
210  The hill formed the full wall on the upper sid...      FLORA  
482  The sunshine strove in vain to gild the dark s...      FLORA  
134  He had directed this officer , with a few horf...      FAUNA  
669  Along this ridge there are magnificent forests...      FLORA  
370  Jetzt wechselt die Landschaft : Gruppen von We...      FLORA  
528  Some of these are : the horned lizard , the we...      FAUNA  
775  Then came rhododendrons of every colour -- pin...      FLORA  
437  De Heer Catesby heeft, in zyne natuurlyke Hift...      FLORA  
381  ) Alysmni argenteum , Silene Ärmeria ' , der s...      FLORA

## Making the Flair Corpus object

The Flair models can be fine-tuned or used for few-shot modelling with TARS with a FLAIR corpus object. This corpus object is made from an IOB-labelled text file.

In [ ]:
# 1. define label names in natural language since some datasets come with cryptic set of labels
label_name_map = {"FLORA": "Flora entities such as plants and fruit",
                  "FAUNA": "Fauna entities such as animals"}

In [ ]:
columns = {0: "text", 1: "bio" }

corpus: Corpus = ColumnCorpus("/content/example_data_CLS/",
                              columns,
                              train_file = "train_fauna_flora.txt",
                              label_name_map = label_name_map)

2024-04-30 15:43:27,928 Reading data from /content/example_data_CLS
2024-04-30 15:43:27,931 Train: /content/example_data_CLS/train_fauna_flora.txt
2024-04-30 15:43:27,932 Dev: None
2024-04-30 15:43:27,933 Test: None
2024-04-30 15:43:28,083 No test split found. Using 0% (i.e. 43 samples) of the train split as test data
2024-04-30 15:43:28,085 No dev split found. Using 0% (i.e. 38 samples) of the train split as dev data


In [ ]:
# 2. what label do we want to predict?
label_type = 'bio'

# 3. make the label dictionary from the corpus
label_dict = corpus.make_label_dictionary(label_type=label_type, add_unk=False)
print(label_dict)

2024-04-30 15:43:32,990 Computing label dictionary. Progress:


0it [00:00, ?it/s]
346it [00:00, 21646.89it/s]

2024-04-30 15:43:33,023 Dictionary created for label 'bio' with 2 values: Fauna entities such as animals (seen 358 times), Flora entities such as plants and fruit (seen 258 times)
Dictionary with 2 tags: Fauna entities such as animals, Flora entities such as plants and fruit


In [ ]:
# init the TARS sequence tagger
tars_tagger: FewshotClassifier = TARSTagger.load('tars-ner')

2024-04-30 15:45:48,152 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity


In [ ]:
# 6. switch to a new task (TARS can do multiple tasks so you must define one)
tars_tagger.add_and_switch_to_new_task(task_name="ner",
                                label_dictionary=label_dict,
                                label_type=label_type,
                                )

# 7. initialize the text classifier trainer
trainer = ModelTrainer(tars_tagger, corpus)

# 8. start the training
trainer.train(base_path='resources/taggers/trec',  # path to store the model artifacts
              learning_rate=0.02,  # use very small learning rate
              mini_batch_size=16,
              mini_batch_chunk_size=4,  # optionally set this if transformer is too much for your machine
              max_epochs=1,  # terminate after 10 epochs
              )

2024-04-30 15:45:52,993 ----------------------------------------------------------------------------------------------------
2024-04-30 15:45:52,999 Model: "TARSTagger(
  (tars_model): SequenceTagger(
    (embeddings): TransformerWordEmbeddings(
      (model): RobertaModel(
        (embeddings): RobertaEmbeddings(
          (word_embeddings): Embedding(50265, 1024, padding_idx=1)
          (position_embeddings): Embedding(514, 1024, padding_idx=1)
          (token_type_embeddings): Embedding(1, 1024)
          (LayerNorm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (dropout): Dropout(p=0.1, inplace=False)
        )
        (encoder): RobertaEncoder(
          (layer): ModuleList(
            (0-23): 24 x RobertaLayer(
              (attention): RobertaAttention(
                (self): RobertaSelfAttention(
                  (query): Linear(in_features=1024, out_features=1024, bias=True)
                  (key): Linear(in_features=1024, out_features=1024, bias=Tru

100%|██████████| 1/1 [00:01<00:00,  1.67s/it]

2024-04-30 15:46:28,535 DEV : loss 0.1813339740037918 - f1-score (micro avg)  0.3455
2024-04-30 15:46:28,540  - 0 epochs without improvement
2024-04-30 15:46:28,544 saving best model


2024-04-30 15:46:43,811 ----------------------------------------------------------------------------------------------------
2024-04-30 15:46:43,820 Loading model from best epoch ...
2024-04-30 15:46:56,185 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity


100%|██████████| 1/1 [00:02<00:00,  2.65s/it]

2024-04-30 15:46:59,438 
Results:
- F-score (micro) 0.48
- F-score (macro) 0.4635
- Accuracy 0.32

By class:
                                         precision    recall  f1-score   support

         Fauna entities such as animals     0.6538    0.4250    0.5152        40
Flora entities such as plants and fruit     0.5385    0.3333    0.4118        21

                              micro avg     0.6154    0.3934    0.4800        61
                              macro avg     0.5962    0.3792    0.4635        61
                           weighted avg     0.6141    0.3934    0.4796        61

2024-04-30 15:46:59,440 ----------------------------------------------------------------------------------------------------


{'test_score': 0.48}

In [ ]:
model_folder = "/content/resources/taggers/trec"

Few_shot_tagger: TARSTagger = TARSTagger.load(os.path.join(model_folder, "best-model.pt"))

2024-04-30 15:51:55,958 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity


In [ ]:
# make a sentence
sentence = Sentence('I saw a weeping willow while passing down the alleyway. The thorns of the roses reminded me of home, in Alabama.')

# predict aspect tags
Few_shot_tagger.predict(sentence)

In [ ]:
print(sentence)

Sentence[24]: "I saw a weeping willow while passing down the alleyway. The thorns of the roses reminded me of home, in Alabama." → ["weeping willow"/Flora entities such as plants and fruit, "roses"/Flora entities such as plants and fruit]


We now performed few-shot classification using TARS!

# Fine-tune TARSTagger from scratch (any language)

In [ ]:
# init the TARS sequence tagger
tars_tagger = TARSTagger(
    'test',
    label_dict,
    label_type='bio',
    embeddings='bert-base-uncased', #This model uses BERT-base-uncased embeddings!
    num_negative_labels_to_sample=1,
    prefix=True,
)

# train the model
trainer = ModelTrainer(tars_tagger, corpus)

trainer.train('resources/taggers/finetuned_tagger_tars',
              learning_rate=0.02,
              mini_batch_size=16,
              mini_batch_chunk_size=1,
              max_epochs=20,
              monitor_test=True,
              embeddings_storage_mode="none",
              )

2024-04-30 15:15:56,042 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity
2024-04-30 15:15:56,051 ----------------------------------------------------------------------------------------------------
2024-04-30 15:15:56,054 Model: "TARSTagger(
  (tars_model): SequenceTagger(
    (embeddings): TransformerWordEmbeddings(
      (model): BertModel(
        (embeddings): BertEmbeddings(
          (word_embeddings): Embedding(30523, 768)
          (position_embeddings): Embedding(512, 768)
          (token_type_embeddings): Embedding(2, 768)
          (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (dropout): Dropout(p=0.1, inplace=False)
        )
        (encoder): BertEncoder(
          (layer): ModuleList(
            (0-11): 12 x BertLayer(
              (attention): BertAttention(
                (self): BertSelfAttention(
                  (query): Linear(in_features=768, out_features=768, bias=True)
                

100%|██████████| 1/1 [00:00<00:00,  1.41it/s]

2024-04-30 15:16:12,799 DEV : loss 0.08356621861457825 - f1-score (micro avg)  0.125



100%|██████████| 1/1 [00:00<00:00,  1.90it/s]

2024-04-30 15:16:13,355 TEST : loss 0.12854349613189697 - f1-score (micro avg)  0.1163
2024-04-30 15:16:13,359  - 0 epochs without improvement
2024-04-30 15:16:13,362 saving best model


...

2024-04-30 15:22:11,021 TEST : loss 0.0989798754453659 - f1-score (micro avg)  0.7662
2024-04-30 15:22:11,027  - 2 epochs without improvement


2024-04-30 15:22:12,658 ----------------------------------------------------------------------------------------------------
2024-04-30 15:22:12,662 Loading model from best epoch ...
2024-04-30 15:22:14,967 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity


100%|██████████| 1/1 [00:00<00:00,  1.55it/s]

2024-04-30 15:22:15,786 
Results:
- F-score (micro) 0.7383
- F-score (macro) 0.7429
- Accuracy 0.5851

By class:
              precision    recall  f1-score   support

       FAUNA     0.7111    0.7273    0.7191        44
       FLORA     0.8214    0.7188    0.7667        32

   micro avg     0.7534    0.7237    0.7383        76
   macro avg     0.7663    0.7230    0.7429        76
weighted avg     0.7576    0.7237    0.7391        76

2024-04-30 15:22:15,789 ----------------------------------------------------------------------------------------------------


{'test_score': 0.738255033557047}

**With only 76 labelled sentences, we managed to fine-tune TARS**! Our final F1 score is a micro average of 0.74, which is pretty impressive for a dataset as small as ours!

Our best model is saved in a new folder (/resources/taggers/few-shot-sequence-tagger). To load it and apply it to our dataset, we can simply run the code below.




---

❗💪🏼 Remember: modelling is experimenting. Flair makes it pretty easy to start modelling and model testing, but the results can always be improved through **hyperparameter tuning, adding more data** or **changing the embeddings used.**. Compare the results when training the model with these tweaked parameters. However, remember that **in order to compare the model, you also have to train and test it on the same splits of your dataset for train and test respectively.**

In [ ]:
model_folder = "'resources/taggers/finetuned_tagger_tars"

tagger: TARSTagger = TARSTagger.load(os.path.join(model_folder, "best-model.pt"))

2024-04-30 15:31:25,073 SequenceTagger predicts: Dictionary with 5 tags: O, S-entity, B-entity, E-entity, I-entity


In [ ]:
# make a sentence
sentence = Sentence('I saw a weeping willow while passing down the alleyway. The thorns of the roses reminded me of home, in Alabama.')

# predict aspect tags
tagger.predict(sentence)

In [ ]:
print(sentence)

Sentence[24]: "I saw a weeping willow while passing down the alleyway. The thorns of the roses reminded me of home, in Alabama." → ["weeping willow"/FLORA, "the"/FLORA, "roses"/FLORA]


# Output of fine-tuned model to CSV

In [ ]:
English_corpus_sample = English_corpus[1:2]

In [ ]:
def ner_custom(text, tagger = tagger):
  sentences = splitter.split(text) # We split the text into sentences to feed to the model.

  #predict tags with custom tagger
  tagger.predict(sentences)

  output = []
  for sentence in sentences:
    for entity in sentence.get_spans():
      ent_label = entity.tag
      ent_text = entity.text

      output.append((ent_label, ent_text, sentence.text))
  return output

In [ ]:
ner_custom("I saw a weeping willow while passing down the alleyway. The thorns of the roses reminded me of home, in Alabama.", tagger = tagger)

[('FLORA',
  'weeping willow',
  'I saw a weeping willow while passing down the alleyway.'),
 ('FLORA', 'of', 'The thorns of the roses reminded me of home, in Alabama.'),
 ('FLORA', 'the', 'The thorns of the roses reminded me of home, in Alabama.'),
 ('FLORA',
  'roses',
  'The thorns of the roses reminded me of home, in Alabama.')]

In [ ]:
# let's apply our custom tagger to a sample of our corpus!

English_corpus_sample['results'] = English_corpus_sample.text.progress_apply(ner_custom)

  0%|          | 0/1 [00:00<?, ?it/s]

2024-04-30 16:10:00,922 Warning: An empty Sentence was created! Are there empty strings in your dataset?
2024-04-30 16:10:13,298 Ignore 1 sentence(s) with no tokens.


<ipython-input-64-1cd00a8c287c>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  English_corpus_sample['results'] = English_corpus_sample.text.progress_apply(ner_custom)


In [ ]:
English_corpus_sample = English_corpus_sample.explode("results")

English_corpus_sample['label'], English_corpus_sample['entity'], English_corpus_sample["sentence"] = zip(*English_corpus_sample.results)

In [ ]:
English_corpus_sample.drop(["results", "text"], inplace = True, axis = 1)

In [ ]:
English_corpus_sample.sample(10)

file language  label     entity  \
31  Studies_of_Travel_Italy.txt  English  FAUNA    dun cow   
31  Studies_of_Travel_Italy.txt  English  FAUNA  lion-like   
31  Studies_of_Travel_Italy.txt  English  FAUNA   Samnites   
31  Studies_of_Travel_Italy.txt  English  FAUNA     animal   
31  Studies_of_Travel_Italy.txt  English  FAUNA    rabbits   
31  Studies_of_Travel_Italy.txt  English  FAUNA        rex   
31  Studies_of_Travel_Italy.txt  English  FAUNA    Serapis   
31  Studies_of_Travel_Italy.txt  English  FLORA       nuts   
31  Studies_of_Travel_Italy.txt  English  FAUNA   monsters   
31  Studies_of_Travel_Italy.txt  English  FAUNA  elephants   

                                             sentence  
31  Procopius saw there the tusks of the Kalydonia...  
31  We hasten to the spot where a lesser Pope than...  
31  In the days of Marius and Sulla, Etruscans and...  
31  A rudely carved bovine animal, in which local ...  
31  The best points for a general view from below ...  
31  But, after all, the "still glassy lake" to whi...  
31  But here we see them within walls reared in ho...  
31  Among other things he ordained that thirty bus...  
31  An elaborate round-headed opening is covered w...  
31  This last has much to show in many ways; most ...

# Train a sequence classifier


Apart from a TarsTagger, we can also train one of Flair's **SequenceTaggers**. This is a different type of tagger architecture made by Flair. If you're interested to see how to train this, check out **ADD LINK TO NOTEBOOK** , where we use the output of our trained aspect tagger to perform **aspect-based sentiment analysis**!